In [0]:
dbutils.widgets.dropdown("time_period","weekly",["weekly",'monthly'])

In [0]:
from datetime import date,timedelta,datetime
from pyspark.sql.functions import * 

time_period= dbutils.widgets.get("time_period")
print(time_period)
today = date.today()

if time_period=='Weekly':
    start_date=today-timedelta(days=today.weekday(),weeks=1)-timedelta(days=1)
    end_date=start_date+timedelta(days=6)

else:
    first=today.replace(day=1)
    end_date=first-timedelta(days=1)
    start_date=first-timedelta(days=end_date.day)

print(start_date,end_date)


monthly
2024-07-01 2024-07-31


In [0]:
df=spark.read.csv("/FileStore/superstore.csv", header=True,inferSchema=True)
display(df)

ID Order_id Order_Date Ship _Date Ship_Mode Customer_id Customer_Name Segment Country City State Postal_Code Region Product_ ID Category Sub_Category Product_Name Sales Quantity Discount Profit user_id state_id order_s 1 CA-2023-152156 2023-11-08 2023-11-11 Second Class CG-12520 Claire Gute Consumer United States Henderson Kentucky 42420 South FUR-BO-10001798 Furniture Bookcases Bush Somerset Collection Bookcase 261.96 2 0 41.9136 null null null 2 CA-2023-152156 2023-11-08 2023-11-11 Second Class CG-12520 Claire Gute Consumer United States Henderson Kentucky 42420 South FUR-CH-10000454 Furniture Chairs Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 731.94 3 0 219.582 1.0 null null 3 CA-2023-138688 2023-06-12 2023-06-16 Second Class DV-13045 Darrin Van Huff Corporate United States Los Angeles California 90036 West OFF-LA-10000240 Office Supplies Labels Self-Adhesive Address Labels for Typewriters by Universal 14.62 2 0 6.8714 null null null 4 US-2022-108966 2022-10-11 2022-10-18 Standard Class SO-20335 Sean O'Donnell Consumer United States Fort Lauderdale Florida 33311 South FUR-TA-10000577 Furniture Tables Bretford CR4500 Series Slim Rectangular Table 957.5775 5 0.45 -383.031 null null null 5 US-2022-108966 2022-10-11 2022-10-18 Standard Class SO-20335 Sean O'Donnell Consumer United States Fort Lauderdale Florida 33311 South OFF-ST-10000760 Office Supplies Storage Eldon Fold 'N Roll Cart System 22.368 2 0.2 2.5164 null null null 6 CA-2021-115812 2021-06-09 2021-06-14 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West FUR-FU-10001487 Furniture Furnishings Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood 48.86 7 0 14.1694 null null null 7 CA-2021-115812 2021-06-09 2021-06-14 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West OFF-AR-10002833 Office Supplies Art Newell 322 7.28 4 0 1.9656 null 1.0 null 8 CA-2021-115812 2021-06-09 2021-06-14 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West TEC-PH-10002275 Technology Phones Mitel 5320 IP Phone VoIP phone 907.152 6 0.2 90.7152 null null null 9 CA-2021-115812 2021-06-09 2021-06-14 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West OFF-BI-10003910 Office Supplies Binders DXL Angle-View Binders with Locking Rings by Samsill 18.504 3 0.2 5.7825 null 2.0 null 10 CA-2021-115812 2021-06-09 2021-06-14 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West OFF-AP-10002892 Office Supplies Appliances Belkin F5C206VTEL 6 Outlet Surge 114.9 5 0 34.47 null null null 11 CA-2021-115812 2021-06-09 2021-06-14 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West FUR-TA-10001539 Furniture Tables Chromcraft Rectangular Conference Tables 1706.184 9 0.2 85.3092 null null null 12 CA-2021-115812 2021-06-09 2021-06-14 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West TEC-PH-10002033 Technology Phones Konftel 250 Conference�phone�- Charcoal black 911.424 4 0.2 68.3568 null null null 13 CA-2024-114412 2024-04-15 2024-04-20 Standard Class AA-10480 Andrew Allen Consumer United States Concord North Carolina 28027 South OFF-PA-10002365 Office Supplies Paper Xerox 1967 15.552 3 0.2 5.4432 null null s 14 CA-2023-161389 2023-12-05 2023-12-10 Standard Class IM-15070 Irene Maddox Consumer United States Seattle Washington 98103 West OFF-BI-10003656 Office Supplies Binders Fellowes PB200 Plastic Comb Binding Machine 407.976 3 0.2 132.5922 null null null 15 US-2022-118983 2022-11-22 2022-11-26 Standard Class HP-14815 Harold Pawlan Home Office United States Fort Worth Texas 76106 Central OFF-AP-10002311 Office Supplies Appliances Holmes Replacement Filter for HEPA Air Cleaner, Very Large Room, HEPA Filter 68.81 5 0.8 -123.858 null null null 16 US-2022-118983 2022-11-22 2022-11-26 St

In [0]:
df.createOrReplaceTempView("superstore")

In [0]:
%sql
select count(distinct customer_id) from superstore

count(DISTINCT customer_id) 793

Static dates

In [0]:
%sql
select count(distinct customer_id) from superstore where order_date between '2024-06-01' and '2024-06-30'

count(DISTINCT customer_id) 118

Dynamic

In [0]:
display(spark.sql(f"""select count(distinct customer_id) from superstore where order_date between '{start_date}' and '{end_date}'"""))

count(DISTINCT customer_id) 102

In [0]:
display(spark.sql(f"""select count(distinct order_id) from superstore where order_date between '{start_date}' and '{end_date}'"""))

count(DISTINCT order_id) 111

In [0]:
%sql
select sum(sales), sum(profit) from superstore

sum(sales) sum(profit) 2272449.8562999545 285707.6050000016

In [0]:
%sql 
select sum(sales), country from superstore group by 2

sum(sales) country 2272449.8562999545 United States

In [0]:
%sql
select sum(sales), country, region from superstore group by 2, 3
order by 1 desc

sum(sales) country region 713471.3445000004 United States West 672194.0539999981 United States East 497800.8728000007 United States Central 388983.58500000037 United States South

In [0]:
%sql
select sum(sales), category from superstore group by 2
order by 1 desc

sum(sales) category 835900.0669999964 Technology 733046.8612999996 Furniture 703502.9280000031 Office Supplies

In [0]:
%sql
select sum(sales), sub_category from superstore group by 2
order by 1 desc limit 10

sum(sales) sub_category 329753.0880000001 Phones 328449.10300000076 Chairs 216803.21200000012 Storage 206965.5320000001 Tables 199905.71700000006 Binders 189238.63099999996 Machines 167380.3180000001 Accessories 149528.02999999994 Copiers 114879.99629999997 Bookcases 107532.161 Appliances

In [0]:
%sql
select sum(sales), product_name from superstore group by 2
order by 1 desc

sum(sales) product_name 61599.824 Canon imageCLASS 2200 Advanced Copier 27453.384 Fellowes PB500 Electric Punch Plastic Comb Binding Machine with Manual Bind 22638.48 Cisco TelePresence System EX90 Videoconferencing Unit 21870.576 HON 5400 Series Task Chairs for Big and Tall 19823.479000000003 GBC DocuBind TL300 Electric Binding System 19024.5 GBC Ibimaster 500 Manual ProClick Binding System 18839.686 Hewlett Packard LaserJet 3310 Copier 18374.895 "HP Designjet T520 Inkjet Large Format Printer - 24"" Color" 17965.068 GBC DocuBind P400 Electric Binding System 17030.311999999998 High Speed Automatic Electric Letter Opener 16829.901 Lexmark MX611dhe Monochrome Laser Printer 16656.199999999997 Martin Yale Chadless Opener Electric Letter Opener 15875.916000000001 Ibico EPK-21 Electric Binding System 15610.9656 Riverside Palais Royal Lawyers Bookcase, Royale Cherry Finish 14299.89 3D Systems Cube Printer, 2nd Generation, Magenta 13943.668000000001 Samsung Galaxy Mega 6.3 12996.600000000002 Apple iPhone 5 12995.291500000001 Bretford Rectangular Conference Table Tops 12975.382 Global Troy Executive Leather Low-Back Tilter 11619.833999999999 Canon PC1060 Personal Laser Copier 11572.78 SAFCO Arco Folding Chair 11304.439999999999 Honeywell Enviracaire Portable HEPA Air Cleaner for 17' x 22' Room 11099.963 Cubify CubeX 3D Printer Double Head Print 11046.609 DMI Eclipse Executive Suite Bookcases 10925.004 Tennsco 6- and 18-Compartment Lockers 10822.359999999999 Plantronics CS510 - Over-the-Head monaural Wireless Headset System 10637.527999999998 Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 10196.604000000003 Logitech�P710e Mobile Speakerphone 9917.64 Chromcraft Bull-Nose Wood Oval Conference Tables & Bases 9630.856 Tennsco Double-Tier Lockers 9544.725 Bush Advantage Collection Racetrack Conference Table 9367.289999999999 Plantronics Savi W720 Multi-Device Wireless Headset System 9279.884 Bady BDG101FRU Card Printer 9158.296 Tennsco Single-Tier Lockers 9070.944000000001 GuestStacker Chair with Chrome Finish Legs 8959.872000000001 Canon Imageclass D680 Copier / Fax 8899.822 Hewlett Packard 610 Color Digital Copier / Printer 8878.4 Wilson Electronics DB Pro Signal Booster 8774.5 Office Star - Professional Matrix Back Chair with 2-to-1 Synchro Tilt and Mesh Fabric Seat 8665.194 Global Deluxe High-Back Manager's Chair 8430.997000000001 Hon 4070 Series Pagoda Armless Upholstered Stacking Chairs 8209.059 Chromcraft Round Conference Tables 8138.232 Hot File 7-Pocket, Floor Stand 8070.192 Fellowes PB300 Plastic Comb Binding Machine 7999.98 Cubify CubeX 3D Printer Triple Head Print 7985.383 Ibico Ibimaster 300 Manual Binding System 7979.4400000000005 Global Commerce Series High-Back Swivel/Tilt Chairs 7834.4 Okidata MB760 Printer 7730.196 Adjustable Depth Letter/Legal Cart 7699.89 Ativa V4110MDD Micro-Cut Shredder 7699.72 Mitel MiVoice 5330e IP Phone 7582.374 Hon 4700 Series Mobuis Mid-Back Task Chairs with Adjustable Arms 7539.7122 Atlantic Metals Mobile 3-Shelf Bookcases, Custom Colors 7515.523999999999 Tennsco 16-Compartment Lockers with Coat Rack 7404.5 Hon 94000 Series Round Tables 7399.704 Logitech diNovo Edge Keyboard 7242.768000000001 Bretford CR4500 Series Slim Rectangular Table 7139.796 Samsung Galaxy S III - 16GB - pebble blue (T-Mobile) 6965.700000000001 Zebra ZM400 Thermal Label Printer 6942.068 Bevis Oval Conference Table, Walnut 6936.102 Hon GuestStacker Chair 6832.908 Hoover Upright Vacuum With Dirt Cup 6819.312000000001 Tennsco Snap-Together Open Shelving Units, Starter Sets and Add-On Units 6785.142 GBC DocuBind 300 Electric Binding Machine 6776.562000000001 Bretford CR8500 Series Meeting Room Furniture 6751.602 Cisco Unified IP Phone 7945G VoIP phone 6748.482000000001 Hon Every-Day Series Multi-Task Chairs 6695.892000000001 ClearOne CHATAttach 160 -�speaker phone 6594.954 Standard Rollaway File with Lock 6584.639999999999 Hon Multipurpose Stacking Arm Chairs 6574.544000000001 Dual Level, Single-Width Filing Carts 65

In [0]:
%sql
select sum(sales), customer_name, city from superstore group by 2, 3
order by 1 desc

sum(sales) customer_name city 23661.228 Sean Miller Jacksonville 18302.37 Tamara Chand Lafayette 14052.48 Raymond Buch Seattle 13723.498000000001 Tom Ashbrook New York City 10539.896 Becky Martin San Antonio 10499.97 Hunter Lopez Newark 9900.19 Sanjit Chand Minneapolis 9892.74 Adrian Barton Detroit 9135.189999999999 Bill Shonely Lakewood 8805.04 Sanjit Engle Arlington 8539.02 Christopher Conant Philadelphia 8319.289999999999 Ken Lonsdale San Francisco 8167.419999999999 Grant Thornton Burlington 7678.228 Peter Fuller New York City 7309.6140000000005 Seth Vernon New York City 6999.96 Tom Boeckenhauer New York City 6486.434 Todd Sumrall New York City 6412.7699999999995 Christopher Martinez Atlanta 6275.476 Nick Crebassa San Francisco 6160.616 Greg Tran Buffalo 6125.822 Karen Daniels Yonkers 5854.194 Keith Dawkins New York City 5802.7 Andy Reiter Jackson 5579.9400000000005 Sean Braxton Houston 5549.41 Daniel Raglin Providence 5325.884 Jane Waco Sacramento 5016.548999999999 Cindy Stewart Lancaster 4940.87 Edward Hooks San Francisco 4909.610000000001 Harry Marie Springfield 4881.1320000000005 Robert Marley Los Angeles 4861.889 Kristen Hastings Springfield 4823.09 Max Jones San Diego 4821.2919999999995 Nathan Mautz New York City 4750.744 Caroline Jumper New York City 4749.327 Joseph Airdo Philadelphia 4685.076 Dennis Pardue North Las Vegas 4630.5105 Nora Preis Fresno 4619.33 Cathy Prescott Springfield 4609.929999999999 Quincy Jones Burlington 4607.2699999999995 Fred Hopkins Seattle 4548.81 John Murray Jamestown 4540.776 Patrick O'Brill Tallahassee 4472.320000000001 Helen Wasserman Indianapolis 4438.686 Adam Bellavance New York City 4419.7699999999995 Pete Kriz New York City 4416.174 Tom Prescott Philadelphia 4409.0199999999995 Clay Ludtke Los Angeles 4406.072 Alex Avila Round Rock 4387.586 Tamara Willingham Seattle 4374.88 Maria Etezadi Henderson 4317.3 Anna H�berlin Springfield 4297.644 Joseph Holt Concord 4283.7919999999995 Darrin Martin New York City 4251.92 Greg Maxwell Alexandria 4190.205999999999 Natalie Fritzler Newark 4189.379999999999 Alan Dominguez Great Falls 4173.812 Karen Ferguson Los Angeles 4142.98 Jim Kriz Seattle 4037.2 Ellis Ballard Seattle 4017.692 Luke Weiss New York City 3999.7900000000004 Corinna Mitchell New York City 3999.7019999999998 Shirley Daniels Midland 3963.57 Laura Armstrong Detroit 3955.5070000000005 Keith Herrera San Francisco 3904.6800000000003 Steven Roelle New York City 3862.0980000000004 Sarah Brown Los Angeles 3793.548 Yana Sorensen Seattle 3747.9300000000003 Katrina Willman Florence 3745.63 Dianna Wilson Lakeville 3740.51 Caroline Jumper Jacksonville 3714.304 Brosina Hoffman Los Angeles 3685.6099999999997 Mitch Webber New York City 3655.112 Ross Baird Philadelphia 3588.096 Susan Pistek Parma 3528.488 Maria Etezadi Santa Barbara 3510.0 Giulietta Baptist Columbia 3508.7940000000003 Maribeth Schnelling Los Angeles 3491.712 Rick Hansen New York City 3480.96 Bill Eplett Jackson 3468.258 Christine Phan New York City 3452.336 Grace Kelly Los Angeles 3397.732 Rick Wilson Brentwood 3385.614 Naresj Patel New York City 3384.518 Natalie Webber New York City 3384.45 Rick Huthwaite Los Angeles 3359.952 Penelope Sewall Los Angeles 3354.98 Kelly Collister San Diego 3339.122 Scot Coram Los Angeles 3333.8999999999996 Mitch Willingham Virginia Beach 3332.974 Peter McVee Dover 3322.576 Tracy Blumstein Philadelphia 3321.278 Ted Trevino Seattle 3291.0699999999997 Thomas Boland Henderson 3290.516 Gary Hwang Seattle 3247.1580000000004 Sample Company A Burbank 3236.41 Mark Cousins Mobile 3209.94 Lena Creighton New York City 3172.707 Rob Lucas Chicago 3165.744 Jim Epp Lakeland 3136.868 Christopher Conant Los Angeles 3116.49 Yoseph Carroll Newark 3115.886 Joseph Holt Seattle 3098.6099999999997 Jim Epp Atlanta 3083.94 Tonja Turnell Richmond 3059.982 Bart Watters Detroit 3036.43 Doug Jacobs New York City 3015.661 Stewart Carmichael Philadelphia 3013.78 Brian Moss Columbia 3002.6499999999996 Bradley Drucker Columbus 2942.78

Databricks visualization. Run in Databricks to view.